In [11]:
import pandas as pd
import numpy as np
import cv2
import csv
import os
import math
import faiss
import keras as k
import keras.backend as K
from keras.layers import merge
from keras.layers.normalization import BatchNormalization
from keras.callbacks import ModelCheckpoint,EarlyStopping,ReduceLROnPlateau
from keras.callbacks import History
from keras.layers import Activation
from keras.models import model_from_json
from keras.optimizers import Adam
from matplotlib import pyplot as plt
from scipy.ndimage import rotate as rot
from sklearn.model_selection import train_test_split
from keras import utils
import numpy as np
import tensorflow as tf
import cv2
import time

Using TensorFlow backend.


In [12]:
train = pd.read_csv('train.csv')
product_attr = pd.read_csv('product_attributes.csv')
images_folder_path = os.getcwd()+'/images/'

In [13]:
def generate_embedding(img,encoder,decoder):
    """Inference the model to generate embedding"""
    start = time.time()
    code = encoder.predict(img[None])[0]  # Generated Embedding
    end = time.time()
    #print(end - start)
    reconstructed = decoder.predict(code[None])[0]
    
    return reconstructed, code

def reset_tf_session():
    K.clear_session()
    tf.reset_default_graph()
    s = K.get_session()
    return s

from keras.models import load_model
s = reset_tf_session()
autoencoder = load_model("hackathon_autoencoder.68-447.31.h5")  
encoder = autoencoder.layers[1]
decoder = autoencoder.layers[2]

In [14]:
def resize_image(img, dim):
    padding = (img.shape[0] - img.shape[1]) / 2
    img=cv2.copyMakeBorder(img, top=0, bottom=0, left=math.floor(padding), right=math.ceil(padding), borderType= cv2.BORDER_CONSTANT, value=[dim,dim,dim])
    # print(img.shape)    
    resized_img = cv2.resize(img, (dim, dim), interpolation=cv2.INTER_AREA)
    return resized_img

# image_list = os.listdir(images_folder_path)


In [15]:
merged_df = pd.merge(train, product_attr, on =['productid'])
images = list(set(merged_df['productid']))
embeding_dict = {}
for image_name in images:
    image = cv2.imread(os.path.join(images_folder_path, str(image_name)+'.jpg'))
    resized_img = resize_image(image, 128)
    reconstructed, code = generate_embedding(resized_img, encoder, decoder)
    embeding_dict[image_name] = list(code)


In [16]:
usr_item_dict = {}
for ids in merged_df.UserId.unique():
    id_set = list(set(merged_df.loc[merged_df['UserId']==ids]['productid']))
    a = list()
    for _id in id_set:
        a.append(embeding_dict[_id])
    avg = np.mean(a, axis = 0)
    usr_item_dict[ids] = avg
    
        
    

In [ ]:
import numpy as np
d = 64                           # dimension
nb = 100000                      # database size
nq = 10000                       # nb of queries
np.random.seed(1234)             # make reproducible
xb = np.random.random((nb, d)).astype('float32')
xb[:, 0] += np.arange(nb) / 1000.
xq = np.random.random((nq, d)).astype('float32')
xq[:, 0] += np.arange(nq) / 1000.

In [46]:
import faiss                   # make faiss available
index = faiss.IndexFlatL2(128)   # build the index
print(index.is_trained)
p = pd.DataFrame(usr_item_dict).T 
k = p.as_matrix()
index.add(k)                  # add vectors to the index
print(index.ntotal)

True
27741


/home/aneesh/Capillary/trainCapillary4/env_new/local/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  """


In [47]:
D, I = index.search(k[:5], 4) # sanity check
print(I)
print(D)

[[   0 1545  189  401]
 [   1  120   71 6908]
 [   2  647  271 2499]
 [   3    6 4380 7783]
 [   4   18   12   15]]
[[    0.       2714.0684   3032.749    3175.8042 ]
 [    0.      10595.975   12127.996   13399.719  ]
 [    0.        710.40564   877.2969   1108.9968 ]
 [    0.       6849.8516   7870.373    8065.7153 ]
 [    0.          0.          0.          0.     ]]


In [63]:
usr_item_dict

{18075: array([-9.9999648e-01,  5.7525169e+01,  4.9030849e+01, -8.2443947e-01,
         4.1459084e+01,  4.0939594e+01, -1.0000000e+00,  7.7723808e+01,
        -1.0000000e+00, -1.0000000e+00, -1.0000000e+00,  7.5129280e+01,
        -1.0000000e+00,  4.3149666e+01, -1.0000000e+00, -1.0000000e+00,
        -1.0000000e+00,  5.0333911e-01, -1.0000000e+00,  4.9665588e+01,
         4.6609711e+01, -1.0000000e+00, -1.0000000e+00,  6.0816383e+01,
         8.0612404e+01,  1.1455286e+00,  5.0558472e+00,  8.9361572e+01,
         6.3574387e+01,  9.0977562e+01, -9.9998337e-01, -1.0000000e+00,
         4.4406555e+01,  6.3538383e+01, -1.0000000e+00,  7.2447800e+01,
         4.8747868e+01,  4.0670666e+01, -8.9369130e-01,  3.8030445e+01,
         6.6639458e+01,  5.8693687e+01, -1.0000000e+00, -1.0000000e+00,
         6.8384232e+01, -1.0000000e+00,  7.2059685e+01, -6.4836979e-01,
         6.1199207e+01, -1.0000000e+00, -1.0000000e+00,  6.6442421e+01,
         5.5181324e+01,  6.6725128e+01,  7.0273651e+01,  

In [49]:
len(merged_df.UserId.unique())

27741

In [65]:
for ind,val in usr_item_dict.items():
#     print (ind,val)
    val1 = np.array(val).reshape(1, 128)
    D, I = index.search(val1, 4)
    
    
    print (D, I, ind)
#     break
    

[[   0.     2714.0684 3032.749  3175.8042]] [[   0 1545  189  401]] 18075
[[    0.    10595.975 12127.996 13399.719]] [[   1  120   71 6908]] 8370
[[   0.       710.40564  877.2969  1108.9968 ]] [[   2  647  271 2499]] 26784
[[   0.     6849.8516 7870.373  8065.7153]] [[   3    6 4380 7783]] 23047
[[0. 0. 0. 0.]] [[ 4 18 12 15]] 19333
[[   0.     6545.9854 8123.159  8781.524 ]] [[   5 1711  288   46]] 21652
[[   0.     5269.302  5869.1387 5986.884 ]] [[   6 4436 3307 7010]] 1973
[[   0.    6188.494 7557.652 7828.245]] [[    7  6847     6 16819]] 4334
[[   0.     2779.4282 3401.408  3595.607 ]] [[   8 4687 3221 1152]] 15930
[[    0.    18358.39  18987.846 19272.035]] [[    9    77 10055 10734]] 16041
[[    0.     8236.821  8899.213 10154.936]] [[   10  6466 11262 12687]] 5385
[[    0.    13264.969 14068.463 16508.992]] [[   11    91 12199  9087]] 27493
[[0. 0. 0. 0.]] [[ 4 18 12 15]] 5423
[[   0.     7824.1826 8727.379  9536.936 ]] [[  13 7204 9243 7904]] 27378
[[   0.     5192.9395 651

[[   0.    8083.891 8484.154 9352.315]] [[  186 11578 11840   284]] 24568
[[   0.     4463.1494 4803.342  5302.082 ]] [[ 187  219 2432 2700]] 5663
[[   0.     2467.2676 3118.1743 3187.3862]] [[ 188 1205  169  147]] 7410
[[   0.     1080.6418 1347.1085 1407.1388]] [[189 271   2 169]] 23447
[[0. 0. 0. 0.]] [[130 140 128 123]] 23788
[[   0.     7297.5664 7620.7676 7878.773 ]] [[ 191 7160 2772 4943]] 10131
[[   0.     3844.1272 4110.458  4653.894 ]] [[ 192  169  401 4095]] 18608
[[   0.     6238.619  6728.8467 7053.5493]] [[  193  2432   444 20156]] 26491
[[    0.    11846.658 12466.68  13015.483]] [[  194 14271 12925  2715]] 7364
[[   0.     3125.7388 3306.6238 3538.3489]] [[ 195  852 5926  544]] 11762
[[    0.     9832.199 10506.655 10799.492]] [[ 196  873 1567  847]] 24617
[[    0.    15391.945 15468.78  15959.162]] [[  197   180 11154  9446]] 19046
[[0. 0. 0. 0.]] [[130 140 128 123]] 21887
[[0. 0. 0. 0.]] [[130 140 128 123]] 19159
[[    0.      6982.2744  9713.371  10493.969 ]] [[  200

[[   0.     4541.5703 5211.4575 5318.051 ]] [[ 376 1647   58  247]] 2492
[[    0.    12408.572 12757.731 13343.363]] [[  377 26617  1271  2076]] 23417
[[    0.      8075.7944 10408.     10577.591 ]] [[  378 16970   381 14541]] 25634
[[   0.     3008.9297 3405.7012 3562.6235]] [[ 379 2645 5087  647]] 10685
[[   0.    8420.655 8917.045 9006.223]] [[ 380 2984 4551 4898]] 15175
[[   0.     7124.3574 7213.6113 7418.926 ]] [[ 381  414 8723 2913]] 21576
[[   0.     3192.2312 4034.8105 4890.1055]] [[  382  2197 23285   163]] 19903
[[   0.     5698.4316 6019.6377 6073.6113]] [[ 383 1040  379 2385]] 1104
[[    0.    15066.279 17092.637 19274.371]] [[  384 16154  4381  4978]] 23048
[[    0.    13938.401 14358.461 14780.6  ]] [[ 385  387 5915 4986]] 12183
[[    0.    26942.234 38487.32  41963.086]] [[386 375 389 387]] 13381
[[    0.    13272.416 13938.401 17749.518]] [[387 389 385 377]] 25341
[[   0.     5662.9824 6146.413  6203.6016]] [[ 388 3287 4950 3697]] 5004
[[    0.    13272.416 17242.074 1

[[    0.    10844.685 11921.182 12089.915]] [[ 563 3755 2374  506]] 3454
[[0. 0. 0. 0.]] [[570 582 580 564]] 26959
[[    0.     9537.943  9643.835 10037.783]] [[  565  2214  2010 24708]] 26629
[[   0.    6772.527 7836.957 8221.161]] [[ 566 2134 2036  594]] 2491
[[    0.    10402.623 10976.44  11459.278]] [[ 567 4907 9160  581]] 10340
[[   0.     2479.7778 2507.607  3003.0671]] [[ 568  261 5570 7601]] 25545
[[    0.    17572.398 19546.223 20665.346]] [[  569 17928 13802 18983]] 14044
[[0. 0. 0. 0.]] [[570 582 580 564]] 23666
[[   0.     7950.1016 8630.567  9361.68  ]] [[571 578 575 586]] 19867
[[   0.     8680.5625 9611.258  9692.338 ]] [[  572  7433 11634  3127]] 26855
[[    0.    17367.898 17612.867 17732.379]] [[  573 13774  1180 17078]] 17254
[[    0.    10281.062 10603.66  11241.875]] [[  574 20656 10717 11089]] 13754
[[   0.     7138.6455 7138.6455 8049.181 ]] [[  575 16812 16811  6834]] 26583
[[   0.     5891.7344 6965.05   7831.121 ]] [[ 576 6699 3360 1188]] 13840
[[    0.    11

[[    0.        0.        0.    25147.031]] [[738 746 728 740]] 23611
[[   0.     4833.6904 5836.887  6487.547 ]] [[ 747 4595  729 6983]] 8073
[[    0.    19992.457 20530.707 21522.7  ]] [[ 748  730 7115 9759]] 7464
[[    0.     9800.943 10550.249 11563.225]] [[  749   741 15337 21452]] 9721
[[    0.     8321.854  9196.273 12052.078]] [[ 750 9767 2927 4349]] 12750
[[    0.    17000.988 23320.11  24631.57 ]] [[ 751 9767  750 7052]] 23431
[[   0.    7691.825 8829.777 8930.908]] [[  752  4460  4587 19710]] 24144
[[    0.     7020.96   9668.641 10849.432]] [[  753 17354  1429   773]] 3877
[[    0.    15932.185 19700.17  24068.594]] [[  754 12019 22251  7244]] 18878
[[    0.    11327.338 11511.98  11588.988]] [[ 755 1452 6365 3185]] 4131
[[    0.    10142.868 10946.395 12739.68 ]] [[  756  7130 17899 18578]] 17568
[[    0.     9791.311 10643.872 10806.229]] [[ 757 3117 2371 5380]] 4589
[[    0.    12939.35  14964.544 15057.159]] [[ 758 5260  549 1863]] 25717
[[   0.     3154.264  3299.208  

...

[[    0.    12472.434 14902.211 15493.511]] [[26853 19717   894 10713]] 26237
[[    0.    16745.277 18656.945 18837.543]] [[26854 20530 21736  4085]] 17968
[[    0.    13353.791 13365.908 13490.744]] [[26855 13646 16321 13635]] 5461
[[    0.    13515.069 14904.689 15670.201]] [[26856  4761   940 16268]] 23650
[[    0.    17530.797 17530.797 17530.797]] [[26857 25281 25293 25287]] 7527
[[    0.     8792.67   9205.355 10079.367]] [[26858 14028  3760  5070]] 16344
[[    0.     12569.359  14646.5205 14833.405 ]] [[26859 24776  8555 19516]] 4472
[[0. 0. 0. 0.]] [[26860 26863 26862 26861]] 27583
[[0. 0. 0. 0.]] [[26860 26863 26862 26861]] 19403
[[0. 0. 0. 0.]] [[26860 26863 26862 26861]] 10187
[[0. 0. 0. 0.]] [[26860 26863 26862 26861]] 13069
[[    0.     9535.903 11122.915 11497.843]] [[26864 26664 16662 27672]] 12190
[[    0.        0.        0.    21565.629]] [[26865 26867 26866   164]] 5146
[[    0.        0.        0.    21565.629]] [[26865 26867 26866   164]] 2729
[[    0.        0.   

[[    0.     9564.309 10694.283 12157.736]] [[27043  2828 12166 10882]] 7785
[[0. 0. 0. 0.]] [[27036 27039 27038 27037]] 27386
[[0. 0. 0. 0.]] [[27036 27039 27038 27037]] 18078
[[0. 0. 0. 0.]] [[27036 27039 27038 27037]] 24222
[[0. 0. 0. 0.]] [[27036 27039 27038 27037]] 1833
[[    0.       0.       0.   26451.76]] [[27048 27050 27049  9909]] 6130
[[    0.       0.       0.   26451.76]] [[27048 27050 27049  9909]] 20599
[[    0.       0.       0.   26451.76]] [[27048 27050 27049  9909]] 19509
[[0. 0. 0. 0.]] [[27051 27055 27054 27053]] 744
[[    0.    18419.441 20226.19  21385.88 ]] [[27052 26754 26440 26466]] 1555
[[0. 0. 0. 0.]] [[27051 27055 27054 27053]] 15317
[[0. 0. 0. 0.]] [[27051 27055 27054 27053]] 17944
[[0. 0. 0. 0.]] [[27051 27055 27054 27053]] 1490
[[    0.    14083.355 15902.397 15902.397]] [[27056  4326 19750 19749]] 13589
[[0. 0. 0. 0.]] [[27051 27055 27054 27053]] 26479
[[    0.        0.    15768.267 17894.562]] [[27058 27059 26468 26464]] 24452
[[    0.        0.    1

[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 18480
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 19405
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 23341
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 5049
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 686
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 14975
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 11670
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 906
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 17218
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 1887
[[0. 0. 0. 0.]] [[27233 27235 27234 27232]] 10431
[[    0.    10838.349 11480.533 12562.728]] [[27247 13834 26249 13810]] 13065
[[    0.    14531.123 15934.67  25400.781]] [[27248 26977 27247 15141]] 19923
[[    0.    18002.906 19670.47  19974.234]] [[27249  1429 20835  6485]] 10524
[[    0.        0.    10969.835 19850.8  ]] [[27251 27250 22952  9956]] 13229
[[    0.        0.    10969.835 19850.8  ]] [[27251 27250 22952  9956]] 8033
[[    0.    10599.545 12010.162 12647.98 ]] [[27252  3655 11008  12

[[0. 0. 0. 0.]] [[27423 27426 27425 27424]] 13728
[[0. 0. 0. 0.]] [[27423 27426 27425 27424]] 21605
[[    0.        0.    32305.082 36047.3  ]] [[27428 27429 11036 19590]] 381
[[    0.        0.    32305.082 36047.3  ]] [[27428 27429 11036 19590]] 1107
[[    0.    28187.201 34366.42  42528.586]] [[27430 24228 22631 19700]] 15441
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 27770
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 3227
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 318
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 7292
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 19769
[[    0.    17101.857 19424.73  29263.465]] [[27436 27035 27447 26173]] 2229
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 19986
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 5800
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 14067
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 15165
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 20098
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 9641
[[0. 0. 0. 0.]] [[27432 27434 27433 27431]] 1583

[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 11427
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 22958
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 827
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 15874
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 2416
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 21157
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 15123
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 14504
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 10457
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 25229
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 1092
[[0. 0. 0. 0.]] [[27616 27619 27618 27617]] 19970
[[    0.    10051.435 11010.098 11968.344]] [[27630 12120  4139  6769]] 10875
[[    0.    15768.066 19541.861 20262.324]] [[27631  3325 12742 23281]] 24352
[[0. 0. 0. 0.]] [[27633 27635 27634 27632]] 15994
[[0. 0. 0. 0.]] [[27633 27635 27634 27632]] 26286
[[0. 0. 0. 0.]] [[27633 27635 27634 27632]] 18643
[[0. 0. 0. 0.]] [[27633 27635 27634 27632]] 10325
[[0. 0. 0. 0.]] [[27637 27639 27638 27636]] 1838

In [87]:
k[1545]

array([-9.9999905e-01,  5.3872524e+01,  5.4134758e+01, -9.7987968e-01,
        3.8265194e+01,  4.5228214e+01, -1.0000000e+00,  7.1981262e+01,
       -1.0000000e+00, -1.0000000e+00, -1.0000000e+00,  8.0958321e+01,
       -4.2734668e-01,  4.3375847e+01,  1.5029061e-01, -1.0000000e+00,
       -1.0000000e+00,  1.4649889e+00, -1.0000000e+00,  4.9620529e+01,
        5.2319580e+01, -9.9999839e-01, -9.6615255e-01,  4.9889671e+01,
        7.7740852e+01,  7.6740807e-01,  3.7228465e+00,  9.0334808e+01,
        6.4237389e+01,  1.0145157e+02, -1.6669409e-01, -1.0000000e+00,
        4.1097801e+01,  6.5390381e+01, -7.2292590e-01,  6.2741409e+01,
        5.3898552e+01,  3.8851051e+01, -6.2268269e-01,  3.7899616e+01,
        5.7649448e+01,  6.3040260e+01, -9.0701133e-01, -1.0000000e+00,
        6.4508476e+01, -1.0000000e+00,  7.2637192e+01, -9.1044319e-01,
        5.7672256e+01, -1.0000000e+00, -1.0000000e+00,  6.9619911e+01,
        5.2330070e+01,  7.4419662e+01,  6.5412025e+01,  7.1107292e+01,
      

In [82]:
p

0           1          2         3          4          5    \
18075  -0.999996   57.525169  49.030849 -0.824439  41.459084  40.939594   
8370   -1.000000   53.249523  69.438522 -1.000000  43.750214  37.402317   
26784  -0.925302   47.681053  56.919086 -0.861398  35.072842  40.765636   
23047  -1.000000   61.675709  16.467894 -1.000000  44.968670  47.074207   
19333  -1.000000   76.278931  -0.965296 -1.000000  55.403179  47.801479   
21652  -1.000000   69.052429  29.934631 -1.000000  25.733292  34.027020   
1973   -1.000000   53.512634  30.783875 -1.000000  40.992130  33.415981   
4334   -1.000000   50.304028  31.866140 -1.000000  30.679749  37.613529   
15930  -1.000000   41.526226  39.033180 -1.000000  24.739313  39.143246   
16041  -1.000000   76.353790  22.542608 -1.000000  65.537514  53.344193   
5385   -1.000000   60.608093  18.687462 -1.000000  34.592907  33.744541   
27493  -0.999999   66.344810  22.011858 -1.000000  27.201599  72.909821   
5423   -1.000000   76.278931  -0.965296 -1.000000  55.403179  47.801479   
27378  -1.000000   64.070511  16.921314 -1.000000  38.940918  39.176311   
21888  -1.000000   42.685505  55.593307 -1.000000  33.112579  37.275501   
16389  -1.000000   76.278931  -0.965296 -1.000000  55.403179  47.801479   
24382  -1.000000   52.294304  27.241251 -1.000000  57.370514  43.665779   
10863  -1.000000   49.196198  32.413544 -1.000000  27.808655  48.016075   
6784   -1.000000   76.278931  -0.965296 -1.000000  55.403179  47.801479   
19222  -1.000000   76.278931  -0.965296 -1.000000  55.403179  47.801479   
22214  -1.000000   35.101231  44.811893 -1.000000  30.144539  41.818630   
15519  -1.000000   65.012375  43.321266 -1.000000  31.716320  32.193535   
21646  -1.000000   51.068668  42.145824 -0.999994  34.158203  38.977898   
4197   -1.000000   66.446205  48.829582 -1.000000  43.768852  38.183685   
18897  -1.000000   49.125679  32.433804 -1.000000  57.417469  46.207096   
7771   -1.000000   87.370728  40.216000 -1.000000  31.690058  48.521057   
12535  -1.000000   60.961777  50.738388 -0.999999  52.124084  42.131989   
22046  -1.000000   37.509125  32.079117 -1.000000  37.303078  29.683048   
6822   -1.000000   76.278931  -0.965296 -1.000000  55.403179  47.801479   
4274   -1.000000   46.680813  47.378361 -1.000000  39.390511  32.238140   
...          ...         ...        ...       ...        ...        ...   
27516  -1.000000   14.016862  64.800156 -1.000000  18.780075   7.136399   
23435  -1.000000   14.016862  64.800156 -1.000000  18.780075   7.136399   
17073  -1.000000    6.859879  93.872108 -1.000000  12.505610  42.546776   
23444  -1.000000   16.213892  68.443321 -1.000000  44.925625  24.283417   
26446  -1.000000   48.619637  67.096344 -1.000000  42.633747  34.196888   
21772  -1.000000   64.783287  41.234787 -1.000000  20.109968  13.553594   
7185   -1.000000   64.783287  41.234787 -1.000000  20.109968  13.553594   
130    -1.000000   46.644257  46.142094 -1.000000  29.398138  20.266457   
431    -1.000000   23.798622  54.005871 -1.000000  37.503815  44.915428   
9877   -1.000000   30.370060  81.483810 -1.000000  45.153919  25.584055   
11597  -1.000000   64.368942  22.900625 -1.000000  49.168541  47.461365   
19763  -1.000000   89.476074  -1.000000 -1.000000  51.343884  59.522118   
14064  -1.000000   89.476074  -1.000000 -1.000000  51.343884  59.522118   
33     -1.000000   89.476074  -1.000000 -1.000000  51.343884  59.522118   
24864  -1.000000   68.433929  91.444305 -1.000000  12.981082  67.846344   
15669  -1.000000  104.116417  53.695206 -1.000000  -1.000000  49.694893   
21443  -1.000000   -0.999987  61.265018 -0.967297  -0.994672  37.395100   
12620  -1.000000   -0.999987  61.265018 -0.967297  -0.994672  37.395100   
18260  -1.000000  115.922386  57.350052 -1.000000  40.175549  96.321129   
19661  -1.000000  107.008705  15.094027 -1.000000  -1.000000  74.909912   
9486   -1.000000   31.472752  47.961006 -1.000000  10.948327  32.057087   
26482  -1.000000  117.403030  70.90657